# TensorFlow basics

In [1]:
# Tensorflow is a library which enables you to build efficient deep learning models.
# You can create models with custom layers, losses, optimizers and more
# TF also provides tools to create custom data processing pipelines

%env TF_CPP_MIN_LOG_LEVEL=3  # silence some TensorFlow warnings and logs.

import numpy as np
import tensorflow as tf

env: TF_CPP_MIN_LOG_LEVEL=3  # silence some TensorFlow warnings and logs.


## Tensor

In [2]:
# Tensors are similar to numpy arrays. They're used to represent inputs and outputs of operations
# You can create tensors from numpy arrays using the convert_to_tensor function

a = np.arange(5)
b = np.ones(5)

a = tf.convert_to_tensor(a)
b = tf.convert_to_tensor(b)

print(a)
print(b)

tf.Tensor([0 1 2 3 4], shape=(5,), dtype=int64)
tf.Tensor([1. 1. 1. 1. 1.], shape=(5,), dtype=float64)


In [3]:
# Tensors support similar operations to numpy arrays
# The syntax is a little different

b = tf.cast(b, tf.int64)
a + b

<tf.Tensor: shape=(5,), dtype=int64, numpy=array([1, 2, 3, 4, 5])>

In [4]:
a = np.arange(24)
a = tf.convert_to_tensor(a)
a = tf.reshape(a, [2, 3, 4])
a

<tf.Tensor: shape=(2, 3, 4), dtype=int64, numpy=
array([[[ 0,  1,  2,  3],
        [ 4,  5,  6,  7],
        [ 8,  9, 10, 11]],

       [[12, 13, 14, 15],
        [16, 17, 18, 19],
        [20, 21, 22, 23]]])>

In [5]:
total = tf.reduce_sum(a)  # similar to numpy.sum
total

<tf.Tensor: shape=(), dtype=int64, numpy=276>

In [6]:
avg = tf.reduce_mean(a, axis=0)
avg

<tf.Tensor: shape=(3, 4), dtype=int64, numpy=
array([[ 6,  7,  8,  9],
       [10, 11, 12, 13],
       [14, 15, 16, 17]])>

## Layer

In [7]:
# Layers are the building blocks of models. You can specify custom layers like so
# Broadly two steps - 1. initialize layer parameters, define trainable weights
# 2. Specify the forward prop operation
# backprop is automatically calculated for you thanks to auto differentiation.

# https://www.tensorflow.org/guide/keras/custom_layers_and_models

class Linear(tf.keras.layers.Layer):
    def __init__(self, units=32, input_dim=32):
        super(Linear, self).__init__()
        w_init = tf.random_normal_initializer()
        self.w = tf.Variable(  # The weights of the layer
            initial_value=w_init(shape=(input_dim, units), dtype="float32"),
            trainable=True,
        )
        b_init = tf.zeros_initializer()
        self.b = tf.Variable(   # bias term
            initial_value=b_init(shape=(units,), dtype="float32"), trainable=True
        )

    def call(self, inputs):  # forward prop
        return tf.matmul(inputs, self.w) + self.b


In [8]:
x = tf.ones((10, 2))
linear_layer = Linear(4, 2)
y = linear_layer(x)
print(y)

tf.Tensor(
[[-0.03293652 -0.02361627 -0.07453395 -0.06298013]
 [-0.03293652 -0.02361627 -0.07453395 -0.06298013]
 [-0.03293652 -0.02361627 -0.07453395 -0.06298013]
 [-0.03293652 -0.02361627 -0.07453395 -0.06298013]
 [-0.03293652 -0.02361627 -0.07453395 -0.06298013]
 [-0.03293652 -0.02361627 -0.07453395 -0.06298013]
 [-0.03293652 -0.02361627 -0.07453395 -0.06298013]
 [-0.03293652 -0.02361627 -0.07453395 -0.06298013]
 [-0.03293652 -0.02361627 -0.07453395 -0.06298013]
 [-0.03293652 -0.02361627 -0.07453395 -0.06298013]], shape=(10, 4), dtype=float32)


In [9]:
# Tensorflow provides a large number of pre-defined layers
# You can use them out of the box instead of having to define them yourself

x = tf.ones((10, 2))
linear_layer = tf.keras.layers.Dense(4)  # built in linear layer
y = linear_layer(x)
print(y)

tf.Tensor(
[[-1.203716    0.44254613  0.6185038  -0.6611192 ]
 [-1.203716    0.44254613  0.6185038  -0.6611192 ]
 [-1.203716    0.44254613  0.6185038  -0.6611192 ]
 [-1.203716    0.44254613  0.6185038  -0.6611192 ]
 [-1.203716    0.44254613  0.6185038  -0.6611192 ]
 [-1.203716    0.44254613  0.6185038  -0.6611192 ]
 [-1.203716    0.44254613  0.6185038  -0.6611192 ]
 [-1.203716    0.44254613  0.6185038  -0.6611192 ]
 [-1.203716    0.44254613  0.6185038  -0.6611192 ]
 [-1.203716    0.44254613  0.6185038  -0.6611192 ]], shape=(10, 4), dtype=float32)


## Model

In [10]:
# A model is a collection of layers which transform the inputs to predictions
# Simple types of models are sequential where there output of one layer feeds into the next

model = tf.keras.models.Sequential([
  tf.keras.layers.Flatten(input_shape=(28, 28, 1)),
  tf.keras.layers.Dense(128, activation="relu"),
  tf.keras.layers.Dense(3, activation="softmax")
])

In [12]:
# You can define custom models similar to custom layers.
# Sublcass Model only if you will be calling fit / predict. Otherwise sublcass layer

class ResNet(tf.keras.Model):

    def __init__(self, num_classes=1000):
        super(ResNet, self).__init__()
        self.block_1 = ResNetBlock()  # a custom layer
        self.block_2 = ResNetBlock()
        self.global_pool = layers.GlobalAveragePooling2D()
        self.classifier = Dense(num_classes)

    def call(self, inputs):  # forward prop through layers
        x = self.block_1(inputs)
        x = self.block_2(x)
        x = self.global_pool(x)
        return self.classifier(x)

In [13]:
# You can call a model on a numpy array or tensor to get the output as a tensor

X = np.random.random((10, 28, 28, 1))
y_pred = model(X).numpy()   # convert output tensor to numpy array
y_pred

array([[0.65325093, 0.10713692, 0.23961219],
       [0.5890078 , 0.13832372, 0.27266842],
       [0.3121852 , 0.21279208, 0.4750228 ],
       [0.55179036, 0.28033993, 0.16786964],
       [0.5258448 , 0.26954064, 0.20461458],
       [0.6607254 , 0.21453238, 0.1247422 ],
       [0.5956045 , 0.21557495, 0.18882057],
       [0.5819955 , 0.19054753, 0.22745697],
       [0.45831108, 0.2663511 , 0.2753378 ],
       [0.6027861 , 0.11960161, 0.2776123 ]], dtype=float32)

# Training a model

In [14]:
# https://www.tensorflow.org/guide/keras/train_and_evaluate
# https://www.tensorflow.org/tutorials/quickstart/beginner

# let's download some data
mnist = tf.keras.datasets.mnist

(x_train, y_train), (x_test, y_test) = mnist.load_data()
x_train, x_test = x_train / 255.0, x_test / 255.0

print(x_train.shape, y_train.shape)

(60000, 28, 28) (60000,)


In [16]:
# create a model

model = tf.keras.models.Sequential([
  tf.keras.layers.Flatten(input_shape=(28, 28)),
  tf.keras.layers.Dense(128, activation='relu'),
  tf.keras.layers.Dropout(0.2),
  tf.keras.layers.Dense(10, activation="softmax")
])

In [17]:
# Specify model training parameters

optimizer = tf.keras.optimizers.Adam(lr=1e-5)
loss = tf.keras.losses.SparseCategoricalCrossentropy()
metrics = ["accuracy"]

model.compile(optimizer, loss, metrics)

In [18]:
# Train the model
# https://www.tensorflow.org/api_docs/python/tf/keras/Model#fit

history = model.fit(x_train, y_train, epochs=5)  # read docs for more params

Epoch 1/5
1875/1875 [==============================] - 3s 2ms/step - loss: 2.0460 - accuracy: 0.3131
Epoch 2/5
1875/1875 [==============================] - 3s 1ms/step - loss: 1.1138 - accuracy: 0.7472
Epoch 3/5
1875/1875 [==============================] - 3s 1ms/step - loss: 0.7590 - accuracy: 0.8133
Epoch 4/5
1875/1875 [==============================] - 3s 1ms/step - loss: 0.6048 - accuracy: 0.8453
Epoch 5/5
1875/1875 [==============================] - 3s 1ms/step - loss: 0.5291 - accuracy: 0.8580


## Dataset objects

In [19]:
# Dataset objects enable you to create efficient data processing pipelines
# You can think of them sort of as data generators
# https://www.tensorflow.org/api_docs/python/tf/data/Dataset

x = np.arange(10).reshape(5,2)
x = tf.convert_to_tensor(x)
x

<tf.Tensor: shape=(5, 2), dtype=int64, numpy=
array([[0, 1],
       [2, 3],
       [4, 5],
       [6, 7],
       [8, 9]])>

In [20]:
# We can create a dataset directly from a tensor.
# The tensor is sliced along axis 0 to yield individual training elements.

dataset = tf.data.Dataset.from_tensor_slices(x)
for element in dataset:
  print(element)

tf.Tensor([0 1], shape=(2,), dtype=int64)
tf.Tensor([2 3], shape=(2,), dtype=int64)
tf.Tensor([4 5], shape=(2,), dtype=int64)
tf.Tensor([6 7], shape=(2,), dtype=int64)
tf.Tensor([8 9], shape=(2,), dtype=int64)


In [21]:
# You can transform items in a dataset as they're being generated
# This example squares elements of each tensor

dataset1 = dataset.map(lambda x: x * x)
for element in dataset1:
  print(element)

tf.Tensor([0 1], shape=(2,), dtype=int64)
tf.Tensor([4 9], shape=(2,), dtype=int64)
tf.Tensor([16 25], shape=(2,), dtype=int64)
tf.Tensor([36 49], shape=(2,), dtype=int64)
tf.Tensor([64 81], shape=(2,), dtype=int64)


In [22]:
# You can shuffle elements in a dataset

dataset2 = dataset1.shuffle(5)
for element in dataset2:
  print(element)

tf.Tensor([36 49], shape=(2,), dtype=int64)
tf.Tensor([4 9], shape=(2,), dtype=int64)
tf.Tensor([0 1], shape=(2,), dtype=int64)
tf.Tensor([64 81], shape=(2,), dtype=int64)
tf.Tensor([16 25], shape=(2,), dtype=int64)


In [23]:
# You can group elements of a dataset to create a batch of inputs
# Here, each batch consists of 2 tensors, each tensor has 2 elements

dataset3 = dataset2.batch(2).prefetch(2)
for element in dataset3:
  print(element)

tf.Tensor(
[[36 49]
 [64 81]], shape=(2, 2), dtype=int64)
tf.Tensor(
[[0 1]
 [4 9]], shape=(2, 2), dtype=int64)
tf.Tensor([[16 25]], shape=(1, 2), dtype=int64)


In [24]:
# You can create a dataset which yields both the inputs as well as target labels as a pair
# A complete pipeline looks something like this

x = np.random.random((10, 5))
y = np.random.random((10, 1))

x = tf.convert_to_tensor(x)
y = tf.convert_to_tensor(y)

xdata = tf.data.Dataset.from_tensor_slices(x)
ydata = tf.data.Dataset.from_tensor_slices(y)

dataset4 = tf.data.Dataset.zip((xdata, ydata))
dataset5 = dataset4.batch(2).prefetch(2)

In [25]:
for element in dataset5:
  print(element[0])
  print(element[1])

tf.Tensor(
[[0.70635636 0.85159591 0.07282059 0.94387339 0.31047997]
 [0.5027618  0.40976972 0.50072862 0.17573116 0.65300608]], shape=(2, 5), dtype=float64)
tf.Tensor(
[[0.39496892]
 [0.08595213]], shape=(2, 1), dtype=float64)
tf.Tensor(
[[0.43742094 0.22395794 0.19410001 0.04797289 0.57758319]
 [0.82328528 0.96187715 0.62288375 0.76993745 0.02660908]], shape=(2, 5), dtype=float64)
tf.Tensor(
[[0.98174687]
 [0.58336443]], shape=(2, 1), dtype=float64)
tf.Tensor(
[[0.32513469 0.63147515 0.89962316 0.34758512 0.35159264]
 [0.35372105 0.44819417 0.49637524 0.35303088 0.08571832]], shape=(2, 5), dtype=float64)
tf.Tensor(
[[0.23170723]
 [0.73871271]], shape=(2, 1), dtype=float64)
tf.Tensor(
[[0.39499834 0.72287297 0.23275004 0.38118985 0.41914835]
 [0.48593847 0.63683236 0.12377803 0.79514066 0.99470932]], shape=(2, 5), dtype=float64)
tf.Tensor(
[[0.12895231]
 [0.71868287]], shape=(2, 1), dtype=float64)
tf.Tensor(
[[0.26353255 0.01301953 0.03679202 0.60177822 0.86128574]
 [0.57731539 0.5275